# Implementing a Physics Informed Neural Network using functorch and comparing it to a regular Neural Network

In [2]:
#importing
import torch
import torch.nn as nn
import torchopt

from functorch import make_functional,  vmap, jacrev

import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go

import pandas as pd
import numpy as np

NOTE: Redirects are currently not supported in Windows or MacOs.


## Time series prediction

### Loading the data

In [3]:
# train data
X = pd.read_csv('../Data/NN data/nn_train_mei_17-26.csv')
X.drop(columns=["Unnamed: 0",  "Water-1", "Water-2", "Water-3"], inplace=True)
X_input = X[['t', 'x', 'y', 'Hot gas pipe', 'Liquid pipe', 'Suction pipe', 'Door', 'Fridge', 'Environment', 'Energy']]
X_output = X[['u']]

# convert to Tensor
X_input = torch.tensor(X_input.values, dtype=torch.float64, requires_grad=True)
X_output = torch.tensor(X_output.values, dtype=torch.float64, requires_grad=True)

In [4]:
# test data
Y = pd.read_csv('../Data/NN data/nn_test_mei_17-26.csv')
Y.drop(columns=["Unnamed: 0", "Water-1", "Water-2", "Water-3"], inplace=True)
Y_input = Y[['t', 'x', 'y', 'Hot gas pipe', 'Liquid pipe', 'Suction pipe', 'Door', 'Fridge', 'Environment', 'Energy']]
Y_output = Y[['u']]

# convert to Tensor
Y_input = torch.tensor(Y_input.values, dtype=torch.float64, requires_grad=True)
Y_output = torch.tensor(Y_output.values, dtype=torch.float64, requires_grad=True)

###  Hyper parameters

In [5]:
# both models
NUM_ITER = 500  # maximum number of iterations
LEARNING_RATE = 0.01  # learning rate
ACT = nn.ReLU() # activation function
DIM_HIDDEN = 64 # dimension of hidden layers

# pinn specific
C = 1 # thermal diffusivity coefficient
BATCH_SIZE = 300 # batch size of the samples
SAMPLE_INTERVAL = 10 # how often the samples are renewed 
ALPHA = 100 # ratio between data and physics
BETA = 100 # ratio between heat and boundary


### Architecture NN

In [6]:
class NN(nn.Module):
    def __init__(
        self,
        input_size: int = 1,
        output_size: int = 1,
        dim_hidden: int = 1,
        act: nn.Module = nn.ReLU(),
    ) -> None:
        """Simple neural network with linear layers and non-linear activation function
        This class is used as universal function approximator for the solution of
        partial differential equations using PINNs
        Args:
            num_inputs (int, optional): The number of input dimensions
            num_outputs (int, optional): The number of outputs of the model, in general is 1
            dim_hidden (int, optional): The number of neurons for each hidden layer
            act (nn.Module, optional): The type of non-linear activation function to be used
        """
        super().__init__()

        self.model = nn.Sequential(
            nn.Linear(input_size, dim_hidden),
            act,
            nn.Linear(dim_hidden, dim_hidden),
            act,
            nn.Linear(dim_hidden, output_size)
        )

    def forward(self, x: torch.Tensor) -> torch.Tensor:
        return self.model(x)

### PINN (defining and training the PINN)
#### Stating the problem
Heat equations are Boundary Value Problems (BVPs) which means that the system must satisfy not only the heat equation but the boundary conditions as well.

All boundary conditions are Neumann type.
##### Heat equation
1. $\frac{\delta u(x,y,t) }{\delta t} = c^2(\frac{\delta^2 u(x,y,t)}{\delta x^2}+\frac{\delta^2 u(x,y,t)}{\delta y^2})$ or $ u_t = c^2 (u_{xx} + u_{yy}) $


##### Boundary Conditions
2. Left side fridge
$ \frac{\delta u(0,y,t)}{\delta x} = 0 $ or $u_x(0, y, t) = 0$
3. Right side fridge
$ \frac{\delta u(length_x,y,t)}{\delta x} = 0 $ or $u_x(length_x, y, t) = 0$
4. Back side fridge
$ \frac{\delta u(x,length_y,t)}{\delta y} = 0 $ or $u_y(x, length_y, t) = 0$
5. Front side fridge.

When door is closed there should be no heat transfer.

$ \frac{\delta u(x,0,t)}{\delta y} = 0 $ or $u_y(x, 0, t) = 0$

When the door is open there should be.

$ u(x,0,t) = outside\_temp$



For each of these four equations the PINN will try to satisfy them as much as possible.
This is done by minimizing the five equations:

1. $u_t - c^2 (u_{xx}+u_{yy})$
2. $u_x(0,y,t)$
3. $u_x(length_x,y,t)$
4. $u_y(x,length_y,t)$
5. $u_y(x,0,t)$ or $u(x,0,t) - outside\_temp$ conditionally on door.

Since these five should all be zero.

#### Generating PDE and Boundary samples

In [7]:
X_BOUNDARY = 82
Y_BOUNDARY = 77
T_END = int((X.shape[0] + Y.shape[0]) / 3 - 1)

rest_features = torch.cat([X_input, Y_input], dim=0)[::3]
rest_features = pd.DataFrame(rest_features.detach().numpy(), columns=['t', 'x', 'y', 'Hot gas pipe', 'Liquid pipe', 'Suction pipe', 'Door', 
                'Fridge', 'Environment', 'Energy'])

def pde_sampling(n = 1000) -> tuple:
    """
    Sample n points in the grid for the PDE
    """
    samples = pd.DataFrame(columns=['t', 'x', 'y', 'Hot gas pipe', 'Liquid pipe', 'Suction pipe', 'Door',
                'Fridge', 'Environment', 'Energy'])

    # sample n points
    for i in range(n):
        sample = np.array([])

        # sample the boundary points
        x_sample = np.random.randint(1, X_BOUNDARY - 1)
        y_sample = np.random.randint(1, Y_BOUNDARY - 1)
        t_sample = np.random.randint(0, T_END)

        sample = np.append(sample, [t_sample, x_sample, y_sample])

        # add the rest of the features, locate the row in the dataframe using t value
        sample = np.append(sample, rest_features.loc[rest_features['t'] == t_sample].values[0][3:])

        # add the sample to the samples array
        samples.loc[i] = sample
    # return tensor that requires grad
    t = torch.tensor(samples.values[:, 0], dtype=torch.float64, requires_grad=True)[:, None]
    x = torch.tensor(samples.values[:, 1], dtype=torch.float64, requires_grad=True)[:, None]
    y = torch.tensor(samples.values[:, 2], dtype=torch.float64, requires_grad=True)[:, None]
    features = torch.tensor(samples.values[:, 3:], dtype=torch.float64, requires_grad=True)
    return t, x, y, features

In [8]:
def boundary_sampling(n : int  = 1000, boundaries : list = ['left', 'right', 'bottom', 'top']) -> list:
    """
    Sample n points in the grid for the boundary conditions
    """
    boundaries_samples = []
    
    # sample n points
    for boundary in ['left', 'right', 'bottom', 'top']:
        samples = pd.DataFrame([], columns=['t', 'x', 'y', 'Hot gas pipe', 'Liquid pipe', 'Suction pipe', 'Door',
                'Fridge', 'Environment', 'Energy'])
        for i in range(int(n/4)):
            sample = np.array([])

            # sample the boundary points
            x_sample = np.random.randint(0, X_BOUNDARY)
            y_sample = np.random.randint(0, Y_BOUNDARY)
            t_sample = np.random.randint(0, T_END)

            if boundary == 'left':
                x_sample = 0
            elif boundary == 'right':
                x_sample = X_BOUNDARY
            elif boundary == 'bottom':
                y_sample = 0
            elif boundary == 'top':
                y_sample = Y_BOUNDARY
            sample = np.append(sample, [t_sample, x_sample, y_sample])

            # add the rest of the features, locate the row in the dataframe using t value
            sample = np.append(sample, rest_features.loc[rest_features['t'] == t_sample].values[0][3:])

            # add the sample to the samples array
            samples.loc[i] = sample

        # make tuple of tensors
        t = torch.tensor(samples.values[:, 0], dtype=torch.float64, requires_grad=True)[:, None]
        x = torch.tensor(samples.values[:, 1], dtype=torch.float64, requires_grad=True)[:, None]
        y = torch.tensor(samples.values[:, 2], dtype=torch.float64, requires_grad=True)[:, None]
        features = torch.tensor(samples.values[:, 3:], dtype=torch.float64, requires_grad=True)
        boundaries_samples.append((t, x, y, features))
    return boundaries_samples

In [12]:
# plot an example of the samples
pde_t, pde_x, pde_y, pde_features = pde_sampling()
pde_samples = torch.cat([pde_t, pde_x, pde_y, pde_features], dim=-1)
boundary_tuples = boundary_sampling()

fig = go.Figure()
fig.add_trace(go.Scatter(x=pde_samples.detach()[:,1], y=pde_samples.detach()[:,2], mode="markers", name="PDE samples"))

for i in range(len(boundary_tuples)):
   bound_t, bound_x, bound_y, bound_features = boundary_tuples[i]
   bound_samples = torch.cat([bound_t, bound_x, bound_y, bound_features], dim=-1)
   fig.add_trace(go.Scatter(x=bound_samples.detach()[:,1], y=bound_samples.detach()[:,2], mode="markers", name=f"Boundary {i} samples"))

fig.update_layout(
          xaxis_title="x",
          yaxis_title="y",
          font=dict(
            family="Courier New, monospace",
            size=18,
            )
)
fig.show()

#### Defining the Loss Functions

In [11]:
# create the PINN model and make it functional using functorch utilities
model_pinn = NN(input_size=10, output_size=1, dim_hidden=DIM_HIDDEN, act=ACT)
model_pinn.double()
fmodel_pinn, params_pinn = make_functional(model_pinn)

# define the u function for the pinn
def u_pinn(t: torch.Tensor, x: torch.Tensor, y: torch.Tensor, rest: torch.Tensor, params: torch.Tensor) -> torch.Tensor:
    input = torch.cat([t, x, y, rest], dim=-1)
    input_ = input.unsqueeze(0)
    u_pred = fmodel_pinn(params, input_).squeeze(0)
    return u_pred

# use `vmap` primitive to allow efficient batching of the input
u_vmap_pinn = vmap(u_pinn, in_dims=(0, 0, 0, 0, None))

dudt = vmap(jacrev(u_pinn, argnums=0), in_dims=(0, 0, 0, 0, None))
dudx = vmap(jacrev(u_pinn, argnums=1), in_dims=(0, 0, 0, 0, None))
dudxdx = vmap(jacrev(jacrev(u_pinn, argnums=1), argnums=1), in_dims=(0, 0, 0, 0, None))
dudy = vmap(jacrev(u_pinn, argnums=2), in_dims=(0, 0, 0, 0, None))
dudydy = vmap(jacrev(jacrev(u_pinn, argnums=2),argnums=2), in_dims=(0, 0, 0, 0, None))


In [13]:
def loss_pde(inputs: tuple, params: torch.Tensor) -> torch.Tensor:
    t, x, y, rest = inputs
    du_dt = dudt(t, x, y, rest, params)
    du_dxdx = dudxdx(t, x, y, rest, params)
    du_dydy = dudydy(t, x, y, rest, params)
    interior = torch.sub(du_dt, torch.mul(torch.add(du_dxdx, du_dydy), (C**2)))
    return nn.MSELoss()(interior, torch.zeros_like(interior))

def loss_boundary_x(inputs: tuple, params: torch.Tensor) -> torch.Tensor:
    t, x, y, rest = inputs
    boundary = dudx(t, x, y, rest, params)
    return nn.MSELoss()(boundary, torch.zeros_like(boundary[0]))

def loss_boundary_y(inputs: tuple, params: torch.Tensor) -> torch.Tensor:
    t, x, y, rest = inputs
    boundary = dudx(t, x, y, rest, params)
    return nn.MSELoss()(boundary, torch.zeros_like(boundary))

def loss_data_pinn(inputs: tuple, params: torch.Tensor, u_real: torch.Tensor) -> torch.Tensor:
    t, x, y, rest = inputs
    u_pred = u_vmap_pinn(t, x, y, rest, params)
    return nn.MSELoss()(u_pred, u_real)

#### Training

In [14]:
# choose optimizer with functional API using functorch
optimizer = torchopt.FuncOptimizer(torchopt.adam(lr=LEARNING_RATE))

# data
train_input = X_input.to(torch.float64)
train_u_real = X_output.to(torch.float64)

# train the model
losses_pinn = np.array([])
for i in range(NUM_ITER):
    # sample PDE and Boundary points
    if i % SAMPLE_INTERVAL == 0:    
        boundary_samples = boundary_sampling(n=BATCH_SIZE)
        pde_samples = pde_sampling(n=BATCH_SIZE)

    #compute the loss from PDE
    pde_loss = loss_pde(pde_samples, params_pinn)

    # compute the loss from boundary conditions
    boundary_loss_x0 = loss_boundary_x(boundary_samples[0], params_pinn)
    boundary_loss_x1 = loss_boundary_x(boundary_samples[1], params_pinn)
    boundary_loss_y0 = loss_boundary_y(boundary_samples[2], params_pinn)
    boundary_loss_y1 = loss_boundary_y(boundary_samples[3], params_pinn)
    boundary_loss = torch.add(torch.add(boundary_loss_x0, boundary_loss_x1), torch.add(boundary_loss_y0, boundary_loss_y1))

    # split the train_input into t, x, y and rest
    t = train_input[:, 0][:, None]
    x = train_input[:, 1][:, None]
    y = train_input[:, 2][:, None]
    rest = train_input[:, 3:]
    train_input_tuple = (t, x, y, rest)

    # compute the loss from data
    data_loss = loss_data_pinn(train_input_tuple, params_pinn, train_u_real)

    # add the losses and optimize
    pinn_loss =  torch.add(data_loss, torch.add(pde_loss, boundary_loss, alpha=BETA), alpha=ALPHA)
    params_pinn = optimizer.step(pinn_loss, params_pinn)

    # store the loss
    losses_pinn = np.append(losses_pinn, [data_loss.item(), pde_loss.item(), boundary_loss.item()])
    print(f"Iteration {i+1} with losses:  Total={pinn_loss.item()}; Data={data_loss}; PDE={pde_loss}; Boundary={boundary_loss}")
    
losses_pinn = losses_pinn.reshape(NUM_ITER,3)    

/usr/local/lib/python3.9/site-packages/torch/nn/modules/loss.py:536: UserWarning:

Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([75, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



Iteration 1 with losses:  Total=5616.172268852989; Data=5612.061232381073; PDE=0.0001673287715872593; Boundary=0.00040943035947574324
Iteration 2 with losses:  Total=97182.18574820706; Data=97156.05900782906; PDE=0.002736976979354182; Boundary=0.0025853042680071595
Iteration 3 with losses:  Total=12931.315843309623; Data=12922.952192238881; PDE=0.0003739357529171351; Boundary=0.0008326257495449864
Iteration 4 with losses:  Total=2663.023493067891; Data=2658.7706951520227; PDE=7.463521218697e-05; Boundary=0.0004245334394649721
Iteration 5 with losses:  Total=13191.152031004402; Data=13190.148508382043; PDE=0.0003776011628634808; Boundary=9.657625060722157e-05
Iteration 6 with losses:  Total=13370.4320195223; Data=13367.848319648561; PDE=0.0003883447676978087; Boundary=0.00025448653969696773
Iteration 7 with losses:  Total=7012.57279984728; Data=7007.944780641711; PDE=0.0002028066416091175; Boundary=0.0004607738541408747
Iteration 8 with losses:  Total=1346.3084865533372; Data=1333.11077

/usr/local/lib/python3.9/site-packages/torch/nn/modules/loss.py:536: UserWarning:

Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([75, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



Iteration 11 with losses:  Total=3392.3376981498827; Data=3374.5908737703944; PDE=0.00012298556964993734; Boundary=0.0017734525822523251
Iteration 12 with losses:  Total=2028.8233096431402; Data=2015.1264431945663; PDE=8.249491542134337e-05; Boundary=0.0013688616957031891
Iteration 13 with losses:  Total=933.0211110466881; Data=925.1030796705529; PDE=4.8323667596725864e-05; Boundary=0.0007913199009375574
Iteration 14 with losses:  Total=256.6641311136065; Data=251.03523529750908; PDE=2.5161173241151857e-05; Boundary=0.0005626379698773314
Iteration 15 with losses:  Total=16.97232539626093; Data=12.294856948861675; PDE=1.3845266893377594e-05; Boundary=0.00046760839207099183
Iteration 16 with losses:  Total=72.83359148260666; Data=68.93988563074429; PDE=1.2496327783060037e-05; Boundary=0.0003892456219084069
Iteration 17 with losses:  Total=261.55916041848945; Data=258.27635120175637; PDE=1.7264542596303028e-05; Boundary=0.000328108276247343
Iteration 18 with losses:  Total=452.49561215018

/usr/local/lib/python3.9/site-packages/torch/nn/modules/loss.py:536: UserWarning:

Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([75, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



...

Iteration 471 with losses:  Total=0.5238493053295608; Data=0.48015940009413227; PDE=2.6422552671404036e-05; Boundary=4.104764996828811e-06
Iteration 472 with losses:  Total=0.521242765281066; Data=0.48167650503130177; PDE=2.499757799313042e-05; Boundary=3.7066502450451103e-06
Iteration 473 with losses:  Total=0.5145024242262192; Data=0.47861945201875083; PDE=2.3100194425880973e-05; Boundary=3.357295276488022e-06
Iteration 474 with losses:  Total=0.5143442610577583; Data=0.48138355696465734; PDE=2.1074871774937122e-05; Boundary=3.0853216915607256e-06
Iteration 475 with losses:  Total=0.5084415391059163; Data=0.47577981365425287; PDE=1.8894526855677818e-05; Boundary=3.077227276609564e-06
Iteration 476 with losses:  Total=0.5119180242571297; Data=0.47699050450199554; PDE=1.7089401845046586e-05; Boundary=3.3218579570629568e-06
Iteration 477 with losses:  Total=0.5144226770565266; Data=0.4789622955068048; PDE=1.5942666765093622e-05; Boundary=3.3866114873212404e-06
Iteration 478 with losses:

/usr/local/lib/python3.9/site-packages/torch/nn/modules/loss.py:536: UserWarning:

Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([75, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



Iteration 481 with losses:  Total=0.5062063631652304; Data=0.4720821067497403; PDE=2.4062395049542962e-05; Boundary=3.1718016910535737e-06
Iteration 482 with losses:  Total=0.506553748844223; Data=0.47269675136547407; PDE=2.436046587827096e-05; Boundary=3.1420950890921837e-06
Iteration 483 with losses:  Total=0.5031054000561926; Data=0.4695688603453076; PDE=2.4982675259140076e-05; Boundary=3.1038272184971085e-06
Iteration 484 with losses:  Total=0.5032576857500554; Data=0.46938505224188964; PDE=2.5437692191006465e-05; Boundary=3.1328864289065023e-06
Iteration 485 with losses:  Total=0.5041254396551413; Data=0.4708156101514093; PDE=2.54656218231668e-05; Boundary=3.076326732141532e-06
Iteration 486 with losses:  Total=0.5021026696477966; Data=0.46890022024376116; PDE=2.521380472435444e-05; Boundary=3.068106893160004e-06
Iteration 487 with losses:  Total=0.5029103735905929; Data=0.46863707988625314; PDE=2.5074070184815835e-05; Boundary=3.17658866858581e-06
Iteration 488 with losses:  Tota

/usr/local/lib/python3.9/site-packages/torch/nn/modules/loss.py:536: UserWarning:

Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([75, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



Iteration 491 with losses:  Total=0.4989235804654329; Data=0.4644262379473649; PDE=3.2540666727538776e-05; Boundary=3.1243275845314166e-06
Iteration 492 with losses:  Total=0.49772922583964574; Data=0.4637671687912021; PDE=3.322165900344511e-05; Boundary=3.0639891148099133e-06
Iteration 493 with losses:  Total=0.4952779336402472; Data=0.4616746147664315; PDE=3.409442662735807e-05; Boundary=3.0193876211079867e-06
Iteration 494 with losses:  Total=0.4930045266339913; Data=0.4597075806408757; PDE=3.496433927318161e-05; Boundary=2.980051206579745e-06
Iteration 495 with losses:  Total=0.4938240468841931; Data=0.46082825332025; PDE=3.557268325938254e-05; Boundary=2.9438525238004865e-06
Iteration 496 with losses:  Total=0.4926710735562769; Data=0.46020114681121566; PDE=3.462670107216622e-05; Boundary=2.9007256637844593e-06
Iteration 497 with losses:  Total=0.49180694734760855; Data=0.4592889761665; PDE=3.467403042264784e-05; Boundary=2.9050568138843743e-06
Iteration 498 with losses:  Total=0.

### Regular NN (defining and training the NN)

In [15]:
model_nn = NN(input_size=10, output_size=1, dim_hidden=DIM_HIDDEN, act=ACT)
fmodel_nn, params_nn = make_functional(model_pinn)

def u_nn(input: torch.Tensor, params: torch.Tensor) -> torch.Tensor:
    # only a single element is supported thus unsqueeze must be applied
    # for batching multiple inputs, `vmap` must be used as below
    input_ = input.unsqueeze(0)
    u_pred = fmodel_nn(params, input_).squeeze(0)
    return u_pred


# use `vmap` primitive to allow efficient batching of the input
u_vmap_nn = vmap(u_nn, in_dims=(0, None))

def loss_data_nn(input: torch.Tensor, params: torch.Tensor, u_real: torch.Tensor) -> torch.Tensor:
    u_pred = u_vmap_nn(input, params)
    return nn.MSELoss()(u_pred, u_real)

/usr/local/lib/python3.9/site-packages/torch/_functorch/deprecated.py:97: UserWarning:

We've integrated functorch into PyTorch. As the final step of the integration, functorch.make_functional is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.functional_call instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html

/usr/local/lib/python3.9/site-packages/torch/_functorch/deprecated.py:58: UserWarning:

We've integrated functorch into PyTorch. As the final step of the integration, functorch.vmap is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.vmap instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html



In [16]:
# choose optimizer with functional API using functorch
optimizer = torchopt.FuncOptimizer(torchopt.adam(lr=LEARNING_RATE))

# data
train_input = X_input.to(torch.float64)
u_real = X_output.to(torch.float64)

# train the model
losses_nn = []
for i in range(NUM_ITER):
    # compute the loss from data
    data_loss = loss_data_nn(train_input, params_nn, u_real)

    # update the parameters using the functional API
    params_nn = optimizer.step(data_loss, params_nn)

    # store the loss
    losses_nn.append([data_loss.item()])
    if i % 10 == 0:
        print(f"Iteration {i+1} with loss {data_loss}")

Iteration 1 with loss 5612.061232381073
Iteration 11 with loss 732.1484802062029
Iteration 21 with loss 427.04926428614925
Iteration 31 with loss 125.97863859583413
Iteration 41 with loss 18.71546107042567
Iteration 51 with loss 5.510048039806166
Iteration 61 with loss 2.102343766594795
Iteration 71 with loss 2.1089420181046505
Iteration 81 with loss 1.748782841188525
Iteration 91 with loss 1.6032564520850554
Iteration 101 with loss 1.5501358532891247
Iteration 111 with loss 1.4686063008668693
Iteration 121 with loss 1.3968791355270829
Iteration 131 with loss 1.3438163055232362
Iteration 141 with loss 1.291820238291558
Iteration 151 with loss 1.2430547426246767
Iteration 161 with loss 1.1968061600262656
Iteration 171 with loss 1.1529929841541469
Iteration 181 with loss 1.1117395537628
Iteration 191 with loss 1.0732608663307783
Iteration 201 with loss 1.0375551663877118
Iteration 211 with loss 1.0045689727242564
Iteration 221 with loss 0.9742345269566071
Iteration 231 with loss 0.946509

### Training results

In [17]:
# plot the loss curve for both models
fig, axs = plt.subplots(1, 2, figsize=(9, 4.5))
axs[0].plot(losses_nn, label="Regular NN")
axs[0].plot(losses_pinn[:, 0], label="PINN")
axs[0].set_xlabel("Iteration")
axs[0].set_ylabel("Loss")
axs[0].set_yscale("log")
axs[0].set_title("(a)")
axs[0].legend()
axs[1].plot(range(100, NUM_ITER), losses_nn[100:], label="Regular NN")
axs[1].plot(range(100, NUM_ITER), losses_pinn[100:, 0], label="PINN")
axs[1].set_xlabel("Iteration")
axs[1].set_ylabel("Loss")
axs[1].set_title("(b)")
axs[1].legend()
plt.savefig("../Media/Plots/Losses2/lossestime")

fig, axs = plt.subplots(1, 2, figsize=(9, 4.5))
axs[0].plot(losses_pinn[:, 0], label="$\mathcal{L}_{data}$")
axs[0].plot(losses_pinn[:, 1], label="$\mathcal{L}_{heat}$")
axs[0].plot(losses_pinn[:, 2], label="$\mathcal{L}_{boundary}$")
axs[0].set_xlabel("Iteration")
axs[0].set_ylabel("Loss")
axs[0].set_yscale('log')
axs[0].set_title("(a)")
axs[0].legend()
axs[1].plot(losses_pinn[:, 0], label=r"$\mathcal{L}_{data}$")
axs[1].plot(losses_pinn[:, 1] * 100, label=r"$\alpha * \mathcal{L}_{heat}$")
axs[1].plot(losses_pinn[:, 2] * 10000, label=r"$\alpha \beta *\mathcal{L}_{boundary}$")
axs[1].set_xlabel("Iteration")
axs[1].set_ylabel("Loss")
axs[1].set_yscale('log')
axs[1].set_title("(b)")
axs[1].legend()
plt.savefig("../Media/Plots/Losses2/pinnlossestime")
plt.show()

In [18]:
train_input = X_input.to(torch.float64)
t = train_input[:, 0][:, None]
x = train_input[:, 1][:, None]
y = train_input[:, 2][:, None]
rest = train_input[:, 3:]

# get final predictions of train data
u_pred_train_nn = u_vmap_nn(train_input, params_nn)
u_pred_train_pinn = u_vmap_pinn(t, x, y, rest, params_pinn)
u_real_train = X_output.to(torch.float64)

print("MSE traindata NN: ", nn.MSELoss()(u_pred_train_nn, u_real_train).item())
print("MSE traindata PINN: ", nn.MSELoss()(u_pred_train_pinn, u_real_train).item())
print("\n")
print("MAE traindata NN: ", nn.L1Loss()(u_pred_train_nn, u_real_train).item())
print("MAE traindata PINN: ", nn.L1Loss()(u_pred_train_pinn, u_real_train).item())

# plot the training results
fig = go.Figure()
fig.add_trace(go.Scatter(x=X_input.detach().numpy()[:, 0], y=u_real_train.detach().numpy()[:, 0], name="Real"))
fig.add_trace(go.Scatter(x=X_input.detach().numpy()[:, 0], y=u_pred_train_nn.detach().numpy()[:,0], name="Regular NN"))
fig.add_trace(go.Scatter(x=X_input.detach().numpy()[:, 0], y=u_pred_train_pinn.detach().numpy()[:,0], name="PINN"))
fig.update_layout(
    xaxis_title="Time",
    yaxis_title="Temperature (C)",
    legend_title="Models",
    font=dict(
        family="Courier New, monospace",
        size=18,
    )
)
fig.show()

MSE traindata NN:  0.6776426900054537
MSE traindata PINN:  0.45585740177826084


MAE traindata NN:  0.5331591488876583
MAE traindata PINN:  0.4015207881609671


### Testing results

In [19]:
test_input = Y_input.to(torch.float64)
t = test_input[:, 0][:, None]
x = test_input[:, 1][:, None]
y = test_input[:, 2][:, None]
rest = test_input[:, 3:]

# get final prediction of test data
u_pred_test_nn = u_vmap_nn(test_input, params_nn)
u_pred_test_pinn = u_vmap_pinn(t, x, y, rest, params_pinn)
u_real_test = Y_output.to(torch.float64)

print("MSE testdata NN: ", nn.MSELoss()(u_pred_test_nn, u_real_test).item())
print("MSE testdata PINN: ", nn.MSELoss()(u_pred_test_pinn, u_real_test).item())
print("\n")
print("MAE testdata NN: ", nn.L1Loss()(u_pred_test_nn, u_real_test).item())
print("MAE testdata PINN: ", nn.L1Loss()(u_pred_test_pinn, u_real_test).item())

# plot the test results
fig = go.Figure()
fig.add_trace(go.Scatter(x=Y_input.detach().numpy()[:, 0], y=u_real_test.detach().numpy()[:, 0], name="Real"))
fig.add_trace(go.Scatter(x=Y_input.detach().numpy()[:, 0], y=u_pred_test_nn.detach().numpy()[:,0], name="Regular NN"))
fig.add_trace(go.Scatter(x=Y_input.detach().numpy()[:, 0], y=u_pred_test_pinn.detach().numpy()[:,0], name="PINN"))
fig.update_layout(
    xaxis_title="Time",
    yaxis_title="Temperature (C)",
    legend_title="Models",
    font=dict(
        family="Courier New, monospace",
        size=18,
    )
)
fig.show()

MSE testdata NN:  41.47102289855315
MSE testdata PINN:  21.28277619546901


MAE testdata NN:  4.894883653816264
MAE testdata PINN:  3.4755297220721353


## Grid prediction

### Loading the data

In [23]:
NUM_ITER = 1000
# merge the original train and test data
old_X = pd.read_csv('../Data/NN data/nn_train_mei_17-26.csv')
old_Y = pd.read_csv('../Data/NN data/nn_test_mei_17-26.csv')
datag = pd.concat([old_X, old_Y], ignore_index=True)
datag.drop(columns=["Unnamed: 0",  "Water-1", "Water-2", "Water-3"], inplace=True)

# split data into X and Y (train and test)
Xg = datag[datag.x != 22]
Yg = datag[datag.x == 22]

Xg_input = Xg[['t', 'x', 'y', 'Hot gas pipe', 'Liquid pipe', 'Suction pipe', 'Door', 'Fridge', 'Environment', 'Energy']]
Xg_output = Xg[['u']]
Yg_input = Yg[['t', 'x', 'y', 'Hot gas pipe', 'Liquid pipe', 'Suction pipe', 'Door', 'Fridge', 'Environment', 'Energy']]
Yg_output = Yg[['u']]

# convert to Tensor
Xg_input = torch.tensor(Xg_input.values, dtype=torch.float64, requires_grad=True)
Xg_output = torch.tensor(Xg_output.values, dtype=torch.float64, requires_grad=True)
Yg_input = torch.tensor(Yg_input.values, dtype=torch.float64, requires_grad=True)
Yg_output = torch.tensor(Yg_output.values, dtype=torch.float64, requires_grad=True)


### PINN

In [24]:
# create the PINN model and make it functional using functorch utilities
modelg_pinn = NN(input_size=10, output_size=1, dim_hidden=DIM_HIDDEN, act=ACT)
modelg_pinn.double()
fmodelg_pinn, paramsg_pinn = make_functional(modelg_pinn)

# define the u function for the pinn
def ug_pinn(t: torch.Tensor, x: torch.Tensor, y: torch.Tensor, rest: torch.Tensor, params: torch.Tensor) -> torch.Tensor:
    input = torch.cat([t, x, y, rest], dim=-1)
    input_ = input.unsqueeze(0)
    u_pred = fmodelg_pinn(params, input_).squeeze(0)
    return u_pred

# use `vmap` primitive to allow efficient batching of the input
u_vmapg_pinn = vmap(ug_pinn, in_dims=(0, 0, 0, 0, None))

dudtg = vmap(jacrev(ug_pinn, argnums=0), in_dims=(0, 0, 0, 0, None))
dudxg = vmap(jacrev(ug_pinn, argnums=1), in_dims=(0, 0, 0, 0, None))
dudxdxg = vmap(jacrev(jacrev(ug_pinn, argnums=1), argnums=1), in_dims=(0, 0, 0, 0, None))
dudyg = vmap(jacrev(ug_pinn, argnums=2), in_dims=(0, 0, 0, 0, None))
dudydyg = vmap(jacrev(jacrev(ug_pinn, argnums=2),argnums=2), in_dims=(0, 0, 0, 0, None))

/usr/local/lib/python3.9/site-packages/torch/_functorch/deprecated.py:97: UserWarning:

We've integrated functorch into PyTorch. As the final step of the integration, functorch.make_functional is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.functional_call instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html

/usr/local/lib/python3.9/site-packages/torch/_functorch/deprecated.py:58: UserWarning:

We've integrated functorch into PyTorch. As the final step of the integration, functorch.vmap is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.vmap instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html

/usr/local/lib/python3.9/site-packages/torch/_functorch/deprecated.py:80: UserWar

In [25]:
def loss_pdeg(inputs: tuple, params: torch.Tensor) -> torch.Tensor:
    t, x, y, rest = inputs
    du_dt = dudtg(t, x, y, rest, params)
    du_dxdx = dudxdxg(t, x, y, rest, params)
    du_dydy = dudydyg(t, x, y, rest, params)
    interior = torch.sub(du_dt, torch.mul(torch.add(du_dxdx, du_dydy), (C**2)))
    return nn.MSELoss()(interior, torch.zeros_like(interior))

def loss_boundary_xg(inputs: tuple, params: torch.Tensor) -> torch.Tensor:
    t, x, y, rest = inputs
    boundary = dudxg(t, x, y, rest, params)
    return nn.MSELoss()(boundary, torch.zeros_like(boundary[0]))

def loss_boundary_yg(inputs: tuple, params: torch.Tensor) -> torch.Tensor:
    t, x, y, rest = inputs
    boundary = dudxg(t, x, y, rest, params)
    return nn.MSELoss()(boundary, torch.zeros_like(boundary))

def loss_datag_pinn(inputs: tuple, params: torch.Tensor, u_real: torch.Tensor) -> torch.Tensor:
    t, x, y, rest = inputs
    u_pred = u_vmapg_pinn(t, x, y, rest, params)
    return nn.MSELoss()(u_pred, u_real)

In [ ]:
# choose optimizer with functional API using functorch
optimizerg = torchopt.FuncOptimizer(torchopt.adam(lr=LEARNING_RATE))

# data
train_input = Xg_input.to(torch.float64)
train_u_real = Xg_output.to(torch.float64)

# train the model
lossesg_pinn = np.array([])
for i in range(NUM_ITER):
    # sample PDE and Boundary points
    if i % SAMPLE_INTERVAL == 0:    
        boundary_samples = boundary_sampling(n=BATCH_SIZE)
        pde_samples = pde_sampling(n=BATCH_SIZE)

    #compute the loss from PDE
    pde_loss = loss_pdeg(pde_samples, paramsg_pinn)

    # compute the loss from boundary conditions
    boundary_loss_x0 = loss_boundary_xg(boundary_samples[0], paramsg_pinn)
    boundary_loss_x1 = loss_boundary_xg(boundary_samples[1], paramsg_pinn)
    boundary_loss_y0 = loss_boundary_yg(boundary_samples[2], paramsg_pinn)
    boundary_loss_y1 = loss_boundary_yg(boundary_samples[3], paramsg_pinn)
    boundary_loss = torch.add(torch.add(boundary_loss_x0, boundary_loss_x1), torch.add(boundary_loss_y0, boundary_loss_y1))

    # split the train_input into t, x, y and rest
    t = train_input[:, 0][:, None]
    x = train_input[:, 1][:, None]
    y = train_input[:, 2][:, None]
    rest = train_input[:, 3:]
    train_input_tuple = (t, x, y, rest)

    # compute the loss from data
    data_loss = loss_datag_pinn(train_input_tuple, paramsg_pinn, train_u_real)

    # add the losses and optimize
    pinn_loss =  torch.add(data_loss, torch.add(pde_loss, boundary_loss, alpha=BETA), alpha=ALPHA)
    paramsg_pinn = optimizerg.step(pinn_loss, paramsg_pinn)

    # store the loss
    lossesg_pinn = np.append(lossesg_pinn, [data_loss.item(), pde_loss.item(), boundary_loss.item()])
    print(f"Iteration {i+1} with losses:  Total={pinn_loss.item()}; Data={data_loss}; PDE={pde_loss}; Boundary={boundary_loss}")
    
lossesg_pinn = lossesg_pinn.reshape(NUM_ITER,3)   

/usr/local/lib/python3.9/site-packages/torch/nn/modules/loss.py:536: UserWarning:

Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([75, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



Iteration 1 with losses:  Total=16069.444370360667; Data=16063.89731146385; PDE=0.0002685233132676847; Boundary=0.0005520206565489505
Iteration 2 with losses:  Total=530883.1769020273; Data=530839.0419873177; PDE=0.010011820560289724; Boundary=0.004313373265351823
Iteration 3 with losses:  Total=36727.20730220734; Data=36713.77104579138; PDE=0.0008522224301506375; Boundary=0.0013351034172947704
Iteration 4 with losses:  Total=52646.642432675406; Data=52615.035465913024; PDE=0.0009691980121402106; Boundary=0.003151004696117044
Iteration 5 with losses:  Total=132670.11433559988; Data=132656.73800453468; PDE=0.0024201766188063916; Boundary=0.001313431340332235
Iteration 6 with losses:  Total=116520.24611956808; Data=116505.78001046205; PDE=0.002110558975718416; Boundary=0.001425505320846072
Iteration 7 with losses:  Total=69618.74650044256; Data=69597.93956022561; PDE=0.0012492586716021528; Boundary=0.0020682014349782283
Iteration 8 with losses:  Total=22611.936086043523; Data=22594.39828

/usr/local/lib/python3.9/site-packages/torch/nn/modules/loss.py:536: UserWarning:

Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([75, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



Iteration 11 with losses:  Total=21916.56321796799; Data=21911.524477995205; PDE=0.00047581411730992785; Boundary=0.000499115856105306
Iteration 12 with losses:  Total=25162.89269851647; Data=25161.021877343122; PDE=0.0005350447883515376; Boundary=0.00018173166945121302
Iteration 13 with losses:  Total=21962.638092061166; Data=21961.279161153176; PDE=0.0004713746632435936; Boundary=0.00013117934416652225
Iteration 14 with losses:  Total=14739.209396669738; Data=14738.00096028695; PDE=0.0003253872417853012; Boundary=0.00011758976586081254
Iteration 15 with losses:  Total=7716.607714154611; Data=7715.318582887152; PDE=0.00017876053785223216; Boundary=0.00012712552136738683
Iteration 16 with losses:  Total=2930.091530330055; Data=2928.5540423461216; PDE=7.607221676660874e-05; Boundary=0.00015298807622566603
Iteration 17 with losses:  Total=582.9054346848337; Data=581.1900554920375; PDE=2.1231109416008613e-05; Boundary=0.0001713256081854715
Iteration 18 with losses:  Total=25.0198081633914

/usr/local/lib/python3.9/site-packages/torch/nn/modules/loss.py:536: UserWarning:

Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([75, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



...

Iteration 361 with losses:  Total=6.331550578431934; Data=6.2490875286515255; PDE=1.4411033680692138e-05; Boundary=8.102194641233937e-06
Iteration 362 with losses:  Total=6.331020960510534; Data=6.237730871342452; PDE=1.4336925437168818e-05; Boundary=9.185639662436488e-06
Iteration 363 with losses:  Total=6.318359225461689; Data=6.224904173893622; PDE=1.4270149020358045e-05; Boundary=9.202803666603157e-06
Iteration 364 with losses:  Total=6.306595067257553; Data=6.213586121380841; PDE=1.3051050495678535e-05; Boundary=9.170384082714437e-06
Iteration 365 with losses:  Total=6.293890999870214; Data=6.202074206155022; PDE=1.3025441366830856e-05; Boundary=9.051424957850954e-06
Iteration 366 with losses:  Total=6.283419235988239; Data=6.1896003005785465; PDE=1.2065607265062485e-05; Boundary=9.261237468318635e-06
Iteration 367 with losses:  Total=6.261207781195632; Data=6.178238049014721; PDE=1.1904654941902119e-05; Boundary=8.177926668672118e-06
Iteration 368 with losses:  Total=6.2488309631

/usr/local/lib/python3.9/site-packages/torch/nn/modules/loss.py:536: UserWarning:

Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([75, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



Iteration 371 with losses:  Total=6.233843570278509; Data=6.131361371094423; PDE=7.597651236575319e-06; Boundary=1.017224340604285e-05
Iteration 372 with losses:  Total=6.2169535147866615; Data=6.119431224917498; PDE=7.571984359834626e-06; Boundary=9.676509143318018e-06
Iteration 373 with losses:  Total=6.20418610821006; Data=6.107474615788079; PDE=7.547583622954694e-06; Boundary=9.59567340596855e-06
Iteration 374 with losses:  Total=6.191942129235082; Data=6.095798058412102; PDE=7.535992518978156e-06; Boundary=9.539047157108237e-06
Iteration 375 with losses:  Total=6.180797274805764; Data=6.083904861041875; PDE=7.524965602012521e-06; Boundary=9.613991720368826e-06
Iteration 376 with losses:  Total=6.16784846531025; Data=6.071711178294884; PDE=7.479015140813304e-06; Boundary=9.53893855012843e-06
Iteration 377 with losses:  Total=6.155223210287988; Data=6.059895279806646; PDE=7.493777468076606e-06; Boundary=9.457855273453428e-06
Iteration 378 with losses:  Total=6.142418325390315; Data=

/usr/local/lib/python3.9/site-packages/torch/nn/modules/loss.py:536: UserWarning:

Using a target size (torch.Size([1, 1])) that is different to the input size (torch.Size([75, 1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.



Iteration 381 with losses:  Total=6.110513594889125; Data=6.011872912723117; PDE=8.204621770667612e-07; Boundary=9.855863594830145e-06
Iteration 382 with losses:  Total=6.099216307975907; Data=5.999833938587961; PDE=8.232577864551138e-07; Boundary=9.930004360930065e-06
Iteration 383 with losses:  Total=6.086715543023989; Data=5.98765984237938; PDE=8.24136504556395e-07; Boundary=9.89732869941536e-06
Iteration 384 with losses:  Total=6.0721129962162035; Data=5.975498752230693; PDE=8.286826803302203e-07; Boundary=9.653137571747794e-06


### Regular NN

In [21]:
modelg_nn = NN(input_size=10, output_size=1, dim_hidden=DIM_HIDDEN, act=ACT)
fmodelg_nn, paramsg_nn = make_functional(modelg_pinn)

def ug_nn(input: torch.Tensor, params: torch.Tensor) -> torch.Tensor:
    # only a single element is supported thus unsqueeze must be applied
    # for batching multiple inputs, `vmap` must be used as below
    input_ = input.unsqueeze(0)
    u_pred = fmodelg_nn(params, input_).squeeze(0)
    return u_pred


# use `vmap` primitive to allow efficient batching of the input
u_vmapg_nn = vmap(ug_nn, in_dims=(0, None))

def loss_datag_nn(input: torch.Tensor, params: torch.Tensor, u_real: torch.Tensor) -> torch.Tensor:
    u_pred = u_vmapg_nn(input, params)
    return nn.MSELoss()(u_pred, u_real)

/usr/local/lib/python3.9/site-packages/torch/_functorch/deprecated.py:97: UserWarning:

We've integrated functorch into PyTorch. As the final step of the integration, functorch.make_functional is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.functional_call instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html

/usr/local/lib/python3.9/site-packages/torch/_functorch/deprecated.py:58: UserWarning:

We've integrated functorch into PyTorch. As the final step of the integration, functorch.vmap is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.vmap instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html



In [ ]:
# choose optimizer with functional API using functorch
optimizer = torchopt.FuncOptimizer(torchopt.adam(lr=LEARNING_RATE))

# data
train_input = Xg_input.to(torch.float64)
u_real = Xg_output.to(torch.float64)

# train the model
lossesg_nn = []
for i in range(NUM_ITER):
    # compute the loss from data
    data_loss = loss_datag_nn(train_input, paramsg_nn, u_real)

    # update the parameters using the functional API
    paramsg_nn = optimizer.step(data_loss, paramsg_nn)

    # store the loss
    lossesg_nn.append([data_loss.item()])
    if i % 10 == 0:
        print(f"Iteration {i+1} with loss {data_loss}")

Iteration 1 with loss 39262.668784622176
Iteration 11 with loss 12210.812285182605
Iteration 21 with loss 291.21410116689407
Iteration 31 with loss 700.8582180627774
Iteration 41 with loss 83.8307340712389
Iteration 51 with loss 17.709113583981143
Iteration 61 with loss 11.110841709654833
Iteration 71 with loss 12.740113557938425
Iteration 81 with loss 9.652571948173556
Iteration 91 with loss 8.769196050874497
Iteration 101 with loss 8.022261150800984
Iteration 111 with loss 7.720580872575366
Iteration 121 with loss 7.608797507367313
Iteration 131 with loss 7.545354967974309
Iteration 141 with loss 7.480803615434729
Iteration 151 with loss 7.426349644002671
Iteration 161 with loss 7.372919749234286
Iteration 171 with loss 7.321650535485095
Iteration 181 with loss 7.269967556523572
Iteration 191 with loss 7.214054365062731
Iteration 201 with loss 7.147790035172405
Iteration 211 with loss 7.086882506701436
Iteration 221 with loss 7.030241641108767
Iteration 231 with loss 16.4185064648882

### Training results

In [ ]:
# plot the loss curve for both models
fig, axs = plt.subplots(1, 2, figsize=(9, 4.5))
axs[0].plot(lossesg_nn, label="Regular NN")
axs[0].plot(lossesg_pinn[:, 0], label="PINN")
axs[0].set_xlabel("Iteration")
axs[0].set_ylabel("Loss")
axs[0].set_yscale("log")
axs[0].set_title("(a)")
axs[0].legend()

axs[1].plot(range(100, NUM_ITER), lossesg_nn[100:], label="Regular NN")
axs[1].plot(range(100, NUM_ITER), lossesg_pinn[100:, 0], label="PINN")
axs[1].set_xlabel("Iteration")
axs[1].set_ylabel("Loss")
axs[1].set_title("(b)")
axs[1].legend()
plt.savefig("../Media/Plots/Losses2/lossesgrid")
plt.show()

fig, axs = plt.subplots(1, 2, figsize=(9, 4.5))
axs[0].plot(lossesg_pinn[:, 0], label="$\mathcal{L}_{data}$")
axs[0].plot(lossesg_pinn[:, 1], label="$\mathcal{L}_{heat}$")
axs[0].plot(lossesg_pinn[:, 2], label="$\mathcal{L}_{boundary}$")
axs[0].set_xlabel("Iteration")
axs[0].set_ylabel("Loss")
axs[0].set_yscale('log')
axs[0].set_title("(a)")
axs[0].legend()

axs[1].plot(lossesg_pinn[:, 0], label=r"$\mathcal{L}_{data}$")
axs[1].plot(lossesg_pinn[:, 1] * 100, label=r"$\alpha * \mathcal{L}_{heat}$")
axs[1].plot(lossesg_pinn[:, 2] * 10000, label=r"$\alpha \beta *\mathcal{L}_{boundary}$")
axs[1].set_xlabel("Iteration")
axs[1].set_ylabel("Loss")
axs[1].set_yscale('log')
axs[1].set_title("(b)")
axs[1].legend()
plt.savefig("../Media/Plots/Losses2/pinnlossesgrid")
plt.show()

In [ ]:
train_input = Xg_input.to(torch.float64)
t = train_input[:, 0][:, None]
x = train_input[:, 1][:, None]
y = train_input[:, 2][:, None]
rest = train_input[:, 3:]

# get final predictions of train data
u_pred_traing_nn = u_vmapg_nn(train_input, paramsg_nn)
u_pred_traing_pinn = u_vmapg_pinn(t, x, y, rest, paramsg_pinn)
u_real_traing = Xg_output.to(torch.float64)

print("MSE traindata NN: ", nn.MSELoss()(u_pred_traing_nn, u_real_traing).item())
print("MSE traindata PINN: ", nn.MSELoss()(u_pred_traing_pinn, u_real_traing).item())
print("\n")
print("MAE traindata NN: ", nn.L1Loss()(u_pred_traing_nn, u_real_traing).item())
print("MAE traindata PINN: ", nn.L1Loss()(u_pred_traing_pinn, u_real_traing).item())

# plot the training results
fig = go.Figure()
fig.add_trace(go.Scatter(x=Xg_input.detach().numpy()[:, 0], y=u_real_traing.detach().numpy()[:, 0], name="Real"))
fig.add_trace(go.Scatter(x=Xg_input.detach().numpy()[:, 0], y=u_pred_traing_nn.detach().numpy()[:,0], name="Regular NN"))
fig.add_trace(go.Scatter(x=Xg_input.detach().numpy()[:, 0], y=u_pred_traing_pinn.detach().numpy()[:,0], name="PINN"))
fig.update_layout(
    xaxis_title="Time",
    yaxis_title="Temperature (C)",
    legend_title="Models",
    font=dict(
        family="Courier New, monospace",
        size=18,
    )
)
fig.show()

### Testing results

In [ ]:
test_input = Yg_input.to(torch.float64)
t = test_input[:, 0][:, None]
x = test_input[:, 1][:, None]
y = test_input[:, 2][:, None]
rest = test_input[:, 3:]

# get final prediction of test data
u_pred_testg_nn = u_vmapg_nn(test_input, paramsg_nn)
u_pred_testg_pinn = u_vmapg_pinn(t, x, y, rest, paramsg_pinn)
u_real_testg = Yg_output.to(torch.float64)

print("MSE testdata NN: ", nn.MSELoss()(u_pred_testg_nn, u_real_testg).item())
print("MSE testdata PINN: ", nn.MSELoss()(u_pred_testg_pinn, u_real_testg).item())
print("\n")
print("MAE testdata NN: ", nn.L1Loss()(u_pred_testg_nn, u_real_testg).item())
print("MAE testdata PINN: ", nn.L1Loss()(u_pred_testg_pinn, u_real_testg).item())

# plot the test results
fig = go.Figure()
fig.add_trace(go.Scatter(x=Yg_input.detach().numpy()[:, 0], y=u_real_testg.detach().numpy()[:, 0], name="Real"))
fig.add_trace(go.Scatter(x=Yg_input.detach().numpy()[:, 0], y=u_pred_testg_nn.detach().numpy()[:,0], name="Regular NN"))
fig.add_trace(go.Scatter(x=Yg_input.detach().numpy()[:, 0], y=u_pred_testg_pinn.detach().numpy()[:,0], name="PINN"))
fig.update_layout(
    xaxis_title="Time",
    yaxis_title="Temperature (C)",
    legend_title="Models",
    font=dict(
        family="Courier New, monospace",
        size=18,
    )
)
fig.show()

### Grid sampling for simulated testing

In [ ]:
# create grid samples for first hour
grid_samples = pd.DataFrame(columns=['t', 'x', 'y'])

# create x, y, t grid
x = np.linspace(0, X_BOUNDARY, int(X_BOUNDARY/2+1))
y = np.linspace(0, Y_BOUNDARY, 15)
t = np.linspace(0, 60, 61)

T, X, Y = np.meshgrid(t, x, y)
x = X.flatten()
y = Y.flatten()
t = T.flatten()

# add the samples to the dataframe
grid_samples['t'] = t
grid_samples['x'] = x
grid_samples['y'] = y

# merge the rest of the features
grid_samples = pd.merge(grid_samples, rest_features.drop(columns=['x', 'y']), on='t')
grid_samples_tensor = torch.tensor(grid_samples.values, dtype=torch.float64)

In [ ]:
# predict the grid temperature using PINN

t = grid_samples_tensor[:, 0][:, None]
x = grid_samples_tensor[:, 1][:, None]
y = grid_samples_tensor[:, 2][:, None]
rest = grid_samples_tensor[:, 3:]

grid_u_pred_pinn = u_vmap_pinn(t, x, y, rest, params_pinn)
u_pinn = grid_u_pred_pinn.detach().numpy()

# make copy of the grid samples
grid_samples_pinn = grid_samples.copy()

grid_samples_pinn['u'] = u_pinn

# animate the prediction on the time t and download the video
fig = px.scatter_3d(grid_samples_pinn, x='x',
                             y='y', 
                             z='u', 
                             # animation
                             animation_frame="t", 
                             # style
                             opacity=0.8,
                             color='u', 
                             color_continuous_scale='Viridis'
                             )
fig.update_layout(title="Grid Prediction using PINN", xaxis_title="x", yaxis_title="y", scene_zaxis_title="Temperature")
fig.write_html("../Plots/Animations/gridpinn.html")
fig.show()


In [ ]:
# predict the grid temperature using NN
grid_u_pred_nn = u_vmap_nn(grid_samples_tensor, params_nn)
u_nn = grid_u_pred_nn.detach().numpy()

# make copy of the grid samples
grid_samples_nn = grid_samples.copy()

grid_samples_nn['u'] = u_nn

# animate the prediction on the time t and download the video
fig = px.scatter_3d(grid_samples_nn, x='x',
                                y='y',
                                z='u',
                                # animation
                                animation_frame="t",
                                # style
                                opacity=0.8,
                                color='u',
                                color_continuous_scale='Viridis'
                                )
fig.update_layout(title="Grid prediction using NN", xaxis_title="x", yaxis_title="y", scene_zaxis_title="Temperature")
fig.write_html("../Plots/Animations/gridnn.html")
fig.show()


In [ ]:
# predict the temperature for the samples
samples_tensor = torch.tensor(samples.values, dtype=torch.float32)
u_pred = u_vmap(samples_tensor, params)
u = u_pred.detach().numpy()

# get prediction for example t 
TIME = 300
example = samples.loc[samples['t'] == TIME]
example = example[['x', 'y']]

example['u'] = u[630*TIME:630*(TIME+1)]
print(example.shape)
 
# plot the prediction for example t
fig = go.Figure()
fig.add_trace(go.Scatter3d(x=example['x'],
                            y=example['y'], 
                            z=example['u'], 
                            name="Prediction",
                            marker=dict(
                                size=12,       
                                color=example['u'],       
                                colorscale='Viridis',
                                opacity=0.8
                            )))
fig.update_layout(title=f"Prediction for t={TIME}", xaxis_title="x", yaxis_title="y", scene_zaxis_title="Temperature")
fig.show()


